# Corona weather analyses
Roald Ruiter, 10 April

## Abstract
Earlier [research](https://www.nature.com/articles/418601a) suggested that heavily reduced air traffic over the US after 9/11 caused larger differences between daily minimum and maximum temperatures. Here I do a similar analyses for the weather over the Netherlands. The clear skies at he beginning of the Corona lockdown (from mid-march) didn't seem to cause a significantly higher temperature difference. However, the second clear period does show one of the highest temperature difference of the 70 year historical data. Futhermore the number of sun hours of both these periods is exceptionaly high. There was no period in the last 70 years which had a comparable number of sun hours. In the period from 21-28 March the average was 11.2 hours.

## Introduction
I noticed that it was very sunny in the Netherlands recently. Then I remembered a [study](https://www.nature.com/articles/418601a) from 2002 where they did a weather analyses of US weather around 9/11. The authors found a significantly larger difference between the daily maximum and minimum temperatures during the three days of heavily reduced air traffic above the US. The effect was partially attributed to a reduction in [contrails](https://en.wikipedia.org/wiki/Contrail). 

## Methods
For the analyses here I pull data from the [API](https://www.knmi.nl/kennis-en-datacentrum/achtergrond/data-ophalen-vanuit-een-script) of the Royal Dutch Meteorology Institute ([KNMI](https://www.knmi.nl/nederland-nu/klimatologie/daggegevens)). Weather data is measured at up to 50 different stations in the period from 1950 to 2020. I averaged the data for all weather stations. The plots show data which has been averaged over a seven day period. The three days before and after a specific data are included in the average.

In [0]:
!pip install astral
!pip install altair_data_server

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import altair as alt
from altair import datum
import requests
from io import StringIO
from astral.geocoder import database, lookup
from astral.sun import daylight

alt.data_transformers.enable('data_server')

DataTransformerRegistry.enable('data_server')

In [0]:
# Get data from KNMI api
payload = {'vars': 'TN:TX:SQ', 'start': '19500101'}
knmi_api_url = 'http://projects.knmi.nl/klimatologie/daggegevens/getdata_dag.cgi'
r = requests.get(knmi_api_url, params=payload)
data_text = r.text

In [0]:
data = StringIO(data_text)
knmi_data = pd.read_csv(data,
    sep=",",
    comment="#",
    header=None, 
    names="""\
station,date,\
min_temp,\
max_temp,\
sun_h""".split(","),
    na_values='     ',
)

In [7]:
# Do some data clean-up, formatting and transformations
knmi_data['date'] = pd.to_datetime(knmi_data["date"], format='%Y%m%d')
knmi_data[[col for col in knmi_data if "temp" in col or 'sun' in col]] /= 10
cols_to_look_for_nas = list(knmi_data)[2:]
knmi_data.dropna(subset=cols_to_look_for_nas, how='all', inplace=True)
knmi_data = knmi_data.groupby('date').mean()
knmi_data.drop(columns='station', inplace=True)
knmi_data['delta_temp'] = knmi_data['max_temp'] - knmi_data['min_temp']
knmi_data['label_2020'] = len(knmi_data) * ['2020']

knmi_data.tail()

min_temp   max_temp      sun_h  delta_temp label_2020
date                                                             
2020-04-05  3.864706  19.923529  12.203125   16.058824       2020
2020-04-06  7.126471  21.826471   9.803125   14.700000       2020
2020-04-07  4.008824  18.620588  11.268750   14.611765       2020
2020-04-08  6.341176  22.241176  11.046875   15.900000       2020
2020-04-09  5.758824  19.270588  10.356250   13.511765       2020

## Results
First I do a similar analyses which was done in the [2002](https://www.nature.com/articles/418601a) study. Below I show the difference between the daily maximum and minimum temperature from 1950 until today. Although an increase in the temperature difference can be seen in the 2020 data, starting from mid-March, it is not significantly higher then many other years. Even if we reduce the sample period to the last 20 years (which probably had comparable air traffic), there are a few years which have much higher temperature differences. However, the second clear period, starting from early Arpril, does show one of the highest temperature differences of the 70 year dataset.

In [8]:
rolling_mean_frame = [-3, 3]

base = alt.Chart(knmi_data.reset_index()
).transform_window(
    rolling_delta_temp=f'mean(delta_temp)',
    frame=rolling_mean_frame
).transform_window(
    rolling_sun_h=f'mean(sun_h)',
    frame=rolling_mean_frame
).transform_calculate(
    year='year(datum.date)'
)

line_2020 = base.mark_line(size=3).encode(
    x='monthdate(date):T',
    y="rolling_delta_temp:Q",
    color=alt.Color(
        'year:N', 
        title='', 
        scale=alt.Scale(
            domain=['2020', '2020'],
            range=['orange', 'orange']
            )
        )
).transform_filter(
    filter='datum.year == 2020'
)

line_old = base.mark_line(opacity=0.4).encode(
    alt.X('monthdate(date):T', title='Months'),
    alt.Y("rolling_delta_temp:Q", title="Temperature difference (°C)"),
    color=alt.Color('year:Q', scale=alt.Scale(scheme="lighttealblue")),
).transform_filter(
    filter='datum.year < 2020'
)

(line_old + line_2020).properties(
    width=800,
    title='Seven day rolling average of difference between minimum and maximum temperature in the Netherlands'
)

alt.LayerChart(...)

Furthermore, if I look at the number of daily sun hours, 2020 really is an outlier. The next highest in the same date range, is almost an hour shorter and does not last as long as the 2020 run.

In [9]:
def sun_hours(city, dates):
    duration_hours = []
    for date in dates:
        start, end = daylight(city, date=date)
        duration = end - start
        duration_hours.append(duration.total_seconds()/3600)
    
    return duration_hours    

amsterdam = lookup("Amsterdam", database())
dates = knmi_data[knmi_data.index.year == 2019].index
daylight_hours = sun_hours(amsterdam.observer, dates)
max_sun_hours = pd.DataFrame(
    [dates, daylight_hours], 
    index=['date', 'sunhours']
).T

max_sun_hours.set_index(['date'], inplace=True)

grouped_sun_hours = max_sun_hours.groupby(
    [max_sun_hours.index.month, max_sun_hours.index.day]
).max()

grouped = knmi_data.groupby([knmi_data.index.month, knmi_data.index.day])
knmi_grouped_sun = grouped["sun_h"].max()
leap_year = knmi_grouped_sun.loc[2, 29]
knmi_grouped_sun = knmi_grouped_sun[knmi_grouped_sun != leap_year].to_frame()

delta = grouped_sun_hours['sunhours'] - knmi_grouped_sun['sun_h']
min_delta = delta.nsmallest(10).mean()

max_sun_hours -= min_delta
max_sun_hours['label_ams'] = len(max_sun_hours) * ['Max sun hours in Amsterdam']

max_sun = alt.Chart(max_sun_hours.reset_index()).mark_line().encode(
    x='monthdate(date):T',
    y='sunhours:Q',
    color=alt.Color('label_ams', title=None, scale=alt.Scale(scheme='greys'))
)

line_2020 = base.mark_line(size=3, color='orange').encode(
    x='monthdate(date):T',
    y="rolling_sun_h:Q",
    color=alt.Color(
        'year:N', 
        title='', 
        scale=alt.Scale(
            domain=['2020', '2020'],
            range=['orange', 'orange']
            )
        )
).transform_filter(
    filter='datum.year == 2020'
)

line_old = base.mark_line(opacity=0.4).encode(
    alt.X('monthdate(date):T', title='Months'),
    alt.Y("rolling_sun_h:Q", title="Sun hours", scale=alt.Scale(domain=(0, 16))),
    color=alt.Color('year:Q', scale=alt.Scale(scheme="lighttealblue")),
).transform_filter(
    filter='datum.year < 2020'
)

(line_old + line_2020 + max_sun).properties(
    width=800,
    title='Seven day rolling average of daily sun hours in the Netherlands'
)

alt.LayerChart(...)

## Conclusions
I'm no expert, so I'm not sure what the results say and if this is compelling evidence for contrail effects on the weather. If there was a clear relationship I would have expected the effect to become larger with time, since air traffic increased quite a bit from 1950 till now.